# 1. Producing the data
In this task, we will implement one Apache Kafka producer to simulate real-time data streaming. Spark is not allowed in this part since it’s simulating a streaming data source.

1.1 Your program should send one batch of click_stream data every 5 seconds. One batch consists of a random 500-1000 rows from the clickstream_rt dataset. The CSV shouldn’t be loaded to memory at once to conserve memory (i.e. Read row as needed).  
1.2 For each row, add an integer column named ‘ts’, a Unix timestamp in seconds since the epoch (UTC timezone). Spead your batch out evenly for 5 seconds.  
For example, if you send a batch of 600 records at 2023-09-01 00:00:00 (ISO format: YYYY-MM-DD HH:MM:SS) -> (ts = 1693526400) :  
Record 1-120: ts = 1693526400  
Record 121-240: ts = 1693526401  
Record 241-360: ts = 1693526402  
….  
1.3 Send your batch to a Kafka topic with an appropriate name.  

All the data except for the ‘ts’ column should be sent in the original String type, without changing to any other types.  


In [1]:
#statements for importing
import pandas as pd
from kafka3 import KafkaProducer
from json import dumps
from time import sleep
import random
from datetime import datetime, timedelta
import csv
import numpy as np
import time
import datetime as dt

#configuation
hostip = "192.168.0.250" #change the IP4 address as needed
#defining the topic
topic = "customer_clickstream_topic"
#defining the broker
bootstrap_servers = f'{hostip}:9092'
file_name = "click_stream_rt.csv"

            
def readCSV(file_name,batch_size):
    file_rows = open(file_name)
    #taking count of rows in the file without header
    count_rows = sum(1 for _ in file_rows) - 1
    #ensuring we read rows based on the batch size and add indexes for rows to be skipped
    skip_rows = sorted(random.sample(range(1, count_rows), count_rows - batch_size))
    #reading the csv file for the specific rows only
    csv_df = pd.read_csv(file_name, skiprows=skip_rows, dtype=str)
    #dropping the first column
    csv_df.drop(csv_df.columns[[0]], axis=1, inplace=True)
    return csv_df

# defining the Kafka producer instance
# using value serializer to serialise the data efore sending it to a kafka topic
def connect_kafka():
    producer = None
    try:
        producer = KafkaProducer(bootstrap_servers=bootstrap_servers, value_serializer=lambda r: dumps(r).encode('utf-8'))
        return producer
    except Exception as e:
        print("Exception while connecting to Kafka")
        print(str(e))
        return None

def publish_message(producer_instance, topic_name, data):
    try:
        #sending the read data to the kafka topic
        producer_instance.send(topic_name, data)
        #successfully sent
        print('Message published successfully. Data: ' + str(data))
    except Exception as ex:
        #handling exception
        print('Exception in publishing message.')
        print(str(ex))

while True:
    batch_size = random.randint(500, 1000)
    read_rows = readCSV(file_name,batch_size)
    #defining clusters for uniform distribution
    cluster = 5
    #diving the rows read into defined clusters
    uniform_cluster = np.array_split(read_rows, cluster)

    #defining current periods for date and time
    current_date = datetime.now()
    current_time = int(time.time())
    for index, part in enumerate(uniform_cluster):
        part['ts'] = int(current_time + index)

    final_df = pd.concat(uniform_cluster, ignore_index=True)  
    #ensuring the data is sent to producer in the correct format
    data_array = final_df.to_dict("records")
    data_array_final = {"click_stream_data": data_array}
    #adding a timestamp for the array
    sent_timestamp = {"sent_timestamp": int(dt.datetime.now().timestamp())}
    #creating a dictionary by joining the timestamp
    data_final = dict(data_array_final, **sent_timestamp)
    #connecting to the producer
    producer = connect_kafka()
    publish_message(producer, topic, data_final)
    sleep (5)


Message published successfully. Data: {'click_stream_data': [{'session_id': '001ea8df-ba11-41cd-8bcc-2b36bc04ee4c', 'event_name': 'SCROLL', 'event_id': '9dc5e025-cf8c-4f31-80e9-dffe9ec63236', 'traffic_source': 'MOBILE', 'event_metadata': nan, 'customer_id': '44024', 'ts': 1697630975}, {'session_id': '00272c5a-b75b-413b-b754-5080fca133bc', 'event_name': 'SEARCH', 'event_id': '83e99d85-7d46-4724-9b24-73e870332885', 'traffic_source': 'MOBILE', 'event_metadata': "{'search_keywords': 'Kaos'}", 'customer_id': '43867', 'ts': 1697630975}, {'session_id': '009993a6-d93b-4343-9fed-7a976b3972ee', 'event_name': 'CLICK', 'event_id': 'd772568f-314c-4da5-a95b-a03236e51039', 'traffic_source': 'WEB', 'event_metadata': nan, 'customer_id': '54908', 'ts': 1697630975}, {'session_id': '00ec5068-3ecf-401a-81f5-8498ce69906c', 'event_name': 'CLICK', 'event_id': '746c03af-73ee-4e92-9006-07b43c041488', 'traffic_source': 'MOBILE', 'event_metadata': nan, 'customer_id': '657', 'ts': 1697630975}, {'session_id': '00f6

Message published successfully. Data: {'click_stream_data': [{'session_id': '012c1ddd-e8e1-415f-a642-6d5ae093ccaa', 'event_name': 'CLICK', 'event_id': 'e519f75d-e4d2-4de6-be25-c566d25b290f', 'traffic_source': 'MOBILE', 'event_metadata': nan, 'customer_id': '17282', 'ts': 1697630981}, {'session_id': '02e7053f-2219-4d80-a390-42fd89af0196', 'event_name': 'CLICK', 'event_id': 'b41592ca-60ab-4240-ab88-e2ff521479be', 'traffic_source': 'MOBILE', 'event_metadata': nan, 'customer_id': '63911', 'ts': 1697630981}, {'session_id': '02e7ae58-de40-4025-a07b-572d4ae08f47', 'event_name': 'CLICK', 'event_id': '0c650fa5-0c9d-4c9b-9199-41de1bcd521b', 'traffic_source': 'MOBILE', 'event_metadata': nan, 'customer_id': '3939', 'ts': 1697630981}, {'session_id': '03741671-fd2e-4d74-a91e-0cbe67d99b1a', 'event_name': 'PURCHASE', 'event_id': '1a64e107-3e8f-4875-9cf2-fd3cf4bea3db', 'traffic_source': 'MOBILE', 'event_metadata': "{'payment_status': 'Success'}", 'customer_id': '84903', 'ts': 1697630981}, {'session_id'

Message published successfully. Data: {'click_stream_data': [{'session_id': '0023dcd9-509d-4752-af5b-02d6369eef5c', 'event_name': 'SCROLL', 'event_id': '4be4fa90-2903-43a7-953f-0a8fc43ae096', 'traffic_source': 'MOBILE', 'event_metadata': nan, 'customer_id': '91500', 'ts': 1697630986}, {'session_id': '003fb07b-0705-4ed6-b64a-2fd2e12c298d', 'event_name': 'PURCHASE', 'event_id': '3da9c87f-d8bc-4f81-b941-9e94698246bb', 'traffic_source': 'MOBILE', 'event_metadata': "{'payment_status': 'Success'}", 'customer_id': '8683', 'ts': 1697630986}, {'session_id': '01d2accc-3d14-4d18-9364-c20ad8da69a5', 'event_name': 'PURCHASE', 'event_id': '1a7ae24a-1c27-45a0-9ade-a2fc558810b0', 'traffic_source': 'MOBILE', 'event_metadata': "{'payment_status': 'Success'}", 'customer_id': '8375', 'ts': 1697630986}, {'session_id': '01f9587e-940a-4272-96ea-9f61bc1310ff', 'event_name': 'SEARCH', 'event_id': '1baccadb-c739-417a-b69d-c1aa827e7405', 'traffic_source': 'MOBILE', 'event_metadata': "{'search_keywords': 'Tas Wan

Message published successfully. Data: {'click_stream_data': [{'session_id': '00272c5a-b75b-413b-b754-5080fca133bc', 'event_name': 'SEARCH', 'event_id': '4b4b1cc3-9cc6-4ae3-aa13-ee82cc72ee5d', 'traffic_source': 'MOBILE', 'event_metadata': "{'search_keywords': 'Kaos'}", 'customer_id': '43867', 'ts': 1697630992}, {'session_id': '011a3d34-7a03-477f-990e-3f86b7e0c868', 'event_name': 'SEARCH', 'event_id': '6596b373-f592-4d6c-aa31-1f9745bfe761', 'traffic_source': 'MOBILE', 'event_metadata': "{'search_keywords': 'Sepatu Nike'}", 'customer_id': '95767', 'ts': 1697630992}, {'session_id': '0138a374-9f40-4eea-9fa4-e8bc592b8905', 'event_name': 'SEARCH', 'event_id': 'd42fcf64-372d-402e-ac0e-5384427be613', 'traffic_source': 'MOBILE', 'event_metadata': "{'search_keywords': 'Thrift'}", 'customer_id': '59147', 'ts': 1697630992}, {'session_id': '01e5e8aa-8a29-4d83-95f4-70557d653163', 'event_name': 'PURCHASE', 'event_id': '8305094a-a3ca-41b3-9bf8-e6ee778c389e', 'traffic_source': 'MOBILE', 'event_metadata'

Message published successfully. Data: {'click_stream_data': [{'session_id': '00b5fc1c-af69-459e-bd16-767e8550edaf', 'event_name': 'ADD_TO_CART', 'event_id': '0e748249-bd24-4682-88c5-55a4668ecee5', 'traffic_source': 'MOBILE', 'event_metadata': "{'product_id': 8332, 'quantity': 1, 'item_price': 276870}", 'customer_id': '47098', 'ts': 1697630997}, {'session_id': '00e0818c-ce09-466b-8fd8-08ace340a28d', 'event_name': 'VIEW_ITEM', 'event_id': 'ed00866e-0287-4703-9164-4b38f9a8fd37', 'traffic_source': 'MOBILE', 'event_metadata': nan, 'customer_id': '4954', 'ts': 1697630997}, {'session_id': '012e03cd-df7e-48e3-9121-54a6d4fa6a3a', 'event_name': 'SEARCH', 'event_id': '9c9d86d1-603e-45aa-9791-b840ca754c97', 'traffic_source': 'MOBILE', 'event_metadata': "{'search_keywords': 'Bekas'}", 'customer_id': '28547', 'ts': 1697630997}, {'session_id': '01b612fc-c1bc-416c-a30e-68b67037b366', 'event_name': 'CLICK', 'event_id': '108dd87e-4d83-47bf-b738-8b56364dc501', 'traffic_source': 'MOBILE', 'event_metadata'

...

Message published successfully. Data: {'click_stream_data': [{'session_id': '01d9f96a-4b9d-4800-8e98-f76d36854fe7', 'event_name': 'ADD_TO_CART', 'event_id': 'fd6a6677-7c03-4032-a7b3-8b24e5683cbe', 'traffic_source': 'MOBILE', 'event_metadata': "{'product_id': 32277, 'quantity': 1, 'item_price': 173112}", 'customer_id': '55882', 'ts': 1697631159}, {'session_id': '021cc629-98e8-487f-938f-b7aa4042032f', 'event_name': 'VIEW_ITEM', 'event_id': 'a914e80a-c75f-4524-b493-5917c666fd41', 'traffic_source': 'MOBILE', 'event_metadata': nan, 'customer_id': '31936', 'ts': 1697631159}, {'session_id': '021ceeb5-e1d4-4ded-94d6-02dfdd7c6fcc', 'event_name': 'PURCHASE', 'event_id': '6a7e5416-dc76-4edf-8216-7615d418aa06', 'traffic_source': 'MOBILE', 'event_metadata': "{'payment_status': 'Success'}", 'customer_id': '2353', 'ts': 1697631159}, {'session_id': '02583350-1165-40f9-be2b-319ae0897220', 'event_name': 'CLICK', 'event_id': '7a8cda6c-185d-4c89-9c6b-2d518e95b56d', 'traffic_source': 'MOBILE', 'event_metad

Message published successfully. Data: {'click_stream_data': [{'session_id': '0023dcd9-509d-4752-af5b-02d6369eef5c', 'event_name': 'SCROLL', 'event_id': 'a459cd14-5369-4f9f-9432-0bdd7dfaa9ea', 'traffic_source': 'MOBILE', 'event_metadata': nan, 'customer_id': '91500', 'ts': 1697631164}, {'session_id': '00633c66-638e-4116-a4de-93221f3656de', 'event_name': 'ADD_TO_CART', 'event_id': 'eea8fe44-fa8e-42b8-b0de-e8899e16b80a', 'traffic_source': 'MOBILE', 'event_metadata': "{'product_id': 14166, 'quantity': 2, 'item_price': 267313}", 'customer_id': '56315', 'ts': 1697631164}, {'session_id': '0174f389-55b5-47eb-9d5b-a07fec783daf', 'event_name': 'HOMEPAGE', 'event_id': '79a1d9f4-93ee-436b-b084-fe24d5790a5f', 'traffic_source': 'MOBILE', 'event_metadata': nan, 'customer_id': '53226', 'ts': 1697631164}, {'session_id': '01edeecd-af17-41a4-9589-7374b1e2e4bd', 'event_name': 'ADD_TO_CART', 'event_id': 'ecfe9e89-f4e6-4a99-99eb-766c5815fbd0', 'traffic_source': 'MOBILE', 'event_metadata': "{'product_id': 21

Message published successfully. Data: {'click_stream_data': [{'session_id': '0023dcd9-509d-4752-af5b-02d6369eef5c', 'event_name': 'CLICK', 'event_id': '5f30cbe9-4fbf-47a2-861b-d08da084f926', 'traffic_source': 'MOBILE', 'event_metadata': nan, 'customer_id': '91500', 'ts': 1697631170}, {'session_id': '0077777f-6e25-40dd-bc18-e3be58b0870d', 'event_name': 'ADD_TO_CART', 'event_id': 'da848cd3-07e6-4706-acd3-6f463701cf88', 'traffic_source': 'WEB', 'event_metadata': "{'product_id': 17710, 'quantity': 1, 'item_price': 171343}", 'customer_id': '58812', 'ts': 1697631170}, {'session_id': '0079deab-6f64-48e2-82e6-9fc97c4eda50', 'event_name': 'VIEW_PROMO', 'event_id': '8625483e-b955-4359-987e-10abf78378b3', 'traffic_source': 'MOBILE', 'event_metadata': nan, 'customer_id': '77609', 'ts': 1697631170}, {'session_id': '00c9e8ff-619d-4371-b4d3-ca3d6f25529f', 'event_name': 'HOMEPAGE', 'event_id': 'f628049c-7adf-45fc-8c73-a24883296d65', 'traffic_source': 'MOBILE', 'event_metadata': nan, 'customer_id': '36

Message published successfully. Data: {'click_stream_data': [{'session_id': '001469b6-e430-49c4-b92e-1095af5586f5', 'event_name': 'SEARCH', 'event_id': '87c09cec-b5bf-43a1-b2ac-30c101fa4d70', 'traffic_source': 'MOBILE', 'event_metadata': "{'search_keywords': 'Bekas'}", 'customer_id': '73032', 'ts': 1697631175}, {'session_id': '00c8774f-9182-4552-a9cf-6eae4ff2f2e8', 'event_name': 'HOMEPAGE', 'event_id': 'ccb7d258-0540-405a-9cef-c5e0017f54bd', 'traffic_source': 'MOBILE', 'event_metadata': nan, 'customer_id': '63969', 'ts': 1697631175}, {'session_id': '00f60471-b607-48fa-8495-32bb96ed9b1a', 'event_name': 'HOMEPAGE', 'event_id': '51a0b788-d77b-46e2-bf31-9e238e0186c2', 'traffic_source': 'MOBILE', 'event_metadata': nan, 'customer_id': '74228', 'ts': 1697631175}, {'session_id': '010c5ba8-adbf-484c-a6e6-67f0ea8c00fa', 'event_name': 'CLICK', 'event_id': 'c236d189-c644-48d2-a94a-ad954702ec67', 'traffic_source': 'MOBILE', 'event_metadata': nan, 'customer_id': '3235', 'ts': 1697631175}, {'session_

KeyboardInterrupt: 